## Addressing Our Architecture Issues
1. **Our sigmoid function squishes predictions between 0 and 1, but our labels are between 2 and -2. How can we fix this?**

Normalize the alarm labels according to our activation function in the prediction layer. For example normalize labels between -1 and 1 if using tanh, or normalize labels between 0 and 1 if using sigmoid.

2. **If we decide to not use multilabel classification and instead train individual networks, is there a library that makes this easier for us?**

Yes, the MultiOutputClassifier class of scikit learn is compatible with Keras classifiers

3. **What is a better accuracy metric to measure model preformance considering data is sparse?**

We can create custom Keras metrics functions to calculate the accuracy for the model in terms of predicting only alarm states that are on

4. **What loss function should we use now that out labels are not 0 and 1?**

Read notebook for my ideas

In [222]:
import torch
import torch.nn as nn
from torch.autograd import Variable

In [5]:
# Option 1
# 81 alarms each with 5 possible states
# multi-hot encoding of length 405
# Train model using binary cross entropy loss on those labels

model = nn.Linear(20, 5) 
x = torch.randn(1, 20)
y = torch.tensor([[0,1,0,1,0]]).float()

criterion = nn.BCEWithLogitsLoss()
optimizer = torch.optim.SGD(model.parameters(), lr=1e-1)

for epoch in range(20):
    optimizer.zero_grad()
    output = (model(x))
    loss = criterion(output, y)
    loss.backward()
    optimizer.step()
    print('Loss: {:.3f}'.format(loss.item()))

Loss: 0.491
Loss: 0.438
Loss: 0.393
Loss: 0.356
Loss: 0.324
Loss: 0.297
Loss: 0.273
Loss: 0.253
Loss: 0.235
Loss: 0.220
Loss: 0.206
Loss: 0.193
Loss: 0.182
Loss: 0.172
Loss: 0.163
Loss: 0.155
Loss: 0.148
Loss: 0.141
Loss: 0.135
Loss: 0.129


In [6]:
# Option 2
# Normalize alarms to be bewteen 0 and 1
# (-2, -1, 0, 1, 2) --> (0, 1, 2, 3, 4) -- > (0., 0.25, 0.50, 0.75, 1.0)
# Train model using binary cross entropy loss on those labels

import numpy as np
from sklearn.preprocessing import MinMaxScaler
labels = np.array([1,2,3,4,5])
scaler = MinMaxScaler()
normed_labels = scaler.fit_transform(labels.reshape(-1, 1))

print("original labels: ", labels)
print("normalized labels: ", normed_labels.reshape(-1))

model = nn.Linear(20, 5) 
x = torch.randn(1, 20)
y = torch.tensor([[0., 0.25, 0.50, 0.75, 1.0]]).float()

criterion = nn.BCEWithLogitsLoss()
optimizer = torch.optim.SGD(model.parameters(), lr=1e-1)

for epoch in range(20):
    optimizer.zero_grad()
    output = (model(x))
    loss = criterion(output, y)
    loss.backward()
    optimizer.step()
    print('Loss: {:.3f}'.format(loss.item()))

original labels:  [1 2 3 4 5]
normalized labels:  [0.   0.25 0.5  0.75 1.  ]
Loss: 0.701
Loss: 0.664
Loss: 0.633
Loss: 0.605
Loss: 0.582
Loss: 0.561
Loss: 0.543
Loss: 0.528
Loss: 0.514
Loss: 0.502
Loss: 0.492
Loss: 0.483
Loss: 0.474
Loss: 0.467
Loss: 0.461
Loss: 0.455
Loss: 0.449
Loss: 0.445
Loss: 0.440
Loss: 0.437


In [7]:
# Option 3
# Create a custom loss function that allows for our original categorical labels
# We could use weighted BCE as a starting point to weight incorrect positive predictions

In [8]:
import numpy as np
np.array([0,0.25,0.5,0,1,0.25])

array([0.  , 0.25, 0.5 , 0.  , 1.  , 0.25])

In [9]:
import pandas as pd

In [10]:
sensors = pd.read_csv('sensors_original.csv')
alarms = pd.read_csv('alarms_filtered.csv')

In [43]:
sensor_id = 'XMEAS 1'
hi = 0.95
lo = 0.05
test_no = 1
features = sensors[sensors['TEST_NO']==test_no][sensor_id]
targets = alarms[alarms['TEST_NO']==test_no][sensor_id]

In [44]:
import plotly.graph_objects as go

In [46]:
fig = go.Figure([
    
    go.Scatter(
        name='XMEAS 1',
        y=features,
        mode='markers+lines',
        marker=dict(color='blue', size=2),
        showlegend=True
    ),
    go.Scatter(
        name='Alarm State',
        y=targets,
        mode='lines',
        marker=dict(color="orange"),
        line=dict(width=1),
        showlegend=True
    ),
    go.Scatter(
        name='Hi',
        y=[hi]*len(features),
        mode='lines',
        marker=dict(color="red"),
        line=dict(width=1),
        showlegend=True
    ),
    go.Scatter(
        name='Lo',
        y=[lo]*len(features),
        mode='lines',
        marker=dict(color="green"),
        line=dict(width=1),
        showlegend=True
    )
])
fig.show()

In [858]:
#Only take first 10k example since this is where the fault occurs
lookback = 1
batch_size = 64
sequences = list(pd.Series(features)[:10000].rolling(window=lookback))
sequences = list(s.to_numpy() for s in sequences)

In [859]:
# We aim to use cross entropy loss for classification of alarm state
# This requires target to be a probability distribtuion
# Accomplish this by converting target to one-hot encoding for each state
# Ex. 1 --> [0, 1, 0, 0, 0]
# Ex. 0 --> [1, 0, 0, 0, 0]
encoded_targets = []
for index, target in enumerate(targets):
#     encoding = np.zeros(5)
#     encoding[target%5] = 1.0
#     encoded_targets.append(encoding)
    encoded_targets.append(target%5)

In [860]:
# Now we have our normalized sensor sequences and encoded targets
# Now we can train model

In [861]:
class LSTM(nn.Module):
    
    def __init__(self, num_classes, input_size, hidden_size, num_layers, sequence_length):
        super(LSTM, self).__init__()
        self.num_classes = num_classes #number of classes
        self.num_layers = num_layers #number of layers
        self.input_size = input_size #input size
        self.hidden_size = hidden_size #hidden state
        self.seq_length = sequence_length #sequence length
        self.lstm = nn.LSTM(
            input_size=input_size, 
            hidden_size=hidden_size, 
            num_layers=num_layers, 
            batch_first=True
        )
        self.fc1 =  nn.Linear(hidden_size, 36) #fully connected 1
        self.fc2 = nn.Linear(36, num_classes) #fully connected last layer
        self.relu = nn.ReLU()
        self.sm = nn.Softmax()
    def forward(self, x):
        h_0 = torch.zeros(self.num_layers, x.size(0), self.hidden_size) #hidden state
        c_0 = torch.zeros(self.num_layers, x.size(0), self.hidden_size) #internal state
#         Propagate input through LSTM
        output, (hn, cn) = self.lstm(x, (h_0, c_0)) #lstm with input, hidden, and internal state
        hn = hn.view(-1, self.hidden_size) #reshaping the data for Dense layer next
        out = self.fc1(hn) #first Dense
        out = self.fc2(out) #Final Output
        out = self.sm(out)
        return out

In [862]:
class Linear(nn.Module):
    
    def __init__(self, num_classes):
        super(Linear, self).__init__()
        self.num_classes = num_classes
        self.fc1 =  nn.Linear(lookback, 5) 
    def forward(self, x):
        x = self.fc1(x) 
        return x

In [863]:
device = 'cuda' if torch.cuda.is_available() else 'cpu'
rnn_model = LSTM(
    num_classes=5,
    num_layers=1,
    input_size=1,
    hidden_size=64,
    sequence_length=lookback
).to(device)
linear_model = Linear(num_classes=5).to(device)

In [864]:
optim = torch.optim.Adam(rnn_model.parameters(), lr=1e-2)

In [865]:
from torch.utils.data import DataLoader

seq_target_pairs = list(zip(sequences[lookback:], encoded_targets[lookback:]))
counts = Counter(list(seq_target_pair[1] for seq_target_pair in seq_target_pairs))
on_count = counts[1]
off_count = counts[0]

while (on_count<=off_count):
    add_ons = list(seq_target_pair for seq_target_pair in seq_target_pairs if seq_target_pair[1]==1)
    on_count=on_count+len(add_ons)
    seq_target_pairs=seq_target_pairs+add_ons

dataset = DataLoader(seq_target_pairs, batch_size=batch_size, shuffle=True, drop_last=True)

In [866]:
states, losses = [], []
for epoch in range(10):
    for batch in dataset:
        preds = rnn_model(batch[0].reshape(batch_size,lookback,1).float())
        optim.zero_grad()
        loss = nn.CrossEntropyLoss()(preds,batch[1])
        loss.backward()
        optim.step()
        losses.append(loss.item())

/Library/Frameworks/Python.framework/Versions/3.7/lib/python3.7/site-packages/ipykernel_launcher.py:28: UserWarning:

Implicit dimension choice for softmax has been deprecated. Change the call to include dim=X as an argument.



In [867]:
fig = go.Figure([
    
    go.Scatter(
        name='loss',
        y=losses,
        mode='markers+lines',
        marker=dict(color='blue', size=2),
        showlegend=True
    )
])
fig.show()

In [891]:
model_filtering = list(x.index(1) for x in rnn_model(torch.tensor(sequences).reshape(len(sequences),lookback,1).float()).round().tolist())

/Library/Frameworks/Python.framework/Versions/3.7/lib/python3.7/site-packages/ipykernel_launcher.py:28: UserWarning:

Implicit dimension choice for softmax has been deprecated. Change the call to include dim=X as an argument.



In [892]:
fig = go.Figure([
    
    go.Scatter(
        name='alarm state',
        y=model_filtering,
        mode='markers+lines',
        marker=dict(color='blue', size=2),
        showlegend=True
    )
])
fig.show()